# **Práctica 8** - Propiedades fotométricas de galaxias de tipo temprano
**Cátedra Sistemas Estelares**

Notebook elaborada por Iván López (2020) y modificada por Gabriel Ferrero (2022, 2023) y Natalia Guevara (2023)


# MUY IMPORTANTE: No correr esta notebook entera.
# NO apretar el botón que dice *"Restart the kernel, then re-run the whole notebook"*


Para conocer más sobre las herramientas usadas, visitar:

*   https://photutils.readthedocs.io/en/stable/isophote.html
*   https://github.com/astropy/photutils-datasets/blob/master/notebooks/isophote/

## Introducción

https://photutils.readthedocs.io/en/stable/api/photutils.isophote.Ellipse.html#photutils.isophote.Ellipse.fit_image


En esta práctica haremos mediciones fotométricas de una galaxia de tipo temprano. Para determinar el brillo superficial de la galaxia en diferentes zonas de la misma, utilizaremos el método dado por [Jedrzejewski (1987; MNRAS 226, 747)](https://ui.adsabs.harvard.edu/abs/1987MNRAS.226..747J/abstract). Este consiste, en esencia, en ajustar isofotas sobre imágenes astronómicas ya reducidas. Las isofotas son curvas cerradas de brillo superficial constante, que en nuestro caso asumiremos que tienen forma elíptica. Caracterizaremos cada isofota a través de los elementos geométricos de la elipse correspondiente, es decir: centro, tamaño de los semiejes y ángulo de posición, más la intensidad de la radiación medida sobre la curva.  

A los efectos del análisis de la variación de los parámetros de las isofotas desde las zonas centrales hacia "afuera" de la imagen de la galaxia, utilizaremos el radio equivalente de las isofotas. Es decir, el radio de un círculo con superficie igual a la de la elipse correspondiente. La relación de tamaños de los semiejes se caracterizará usando un parámetro denominado *elipticidad*.

Durante el curso del ajuste, para un dado semieje mayor (fijo), primero se hace una aproximación inicial de la elipticidad, el ángulo de posición de la elipse y la posición en la imagen del centro de la misma. Luego, se muestrea la intensidad a lo largo del camino elíptico para distintos valores de anomalía excéntrica. Esto dará una tabla de la intensidad versus la anomalía. A esa tabla se le ajusta por mínimos cuadrados una función unidimensional, representada por una serie de Fourier. Es decir que se supone

$$ I = I_0 + \sum_{n=1}^{\infty} (A_n\,\mathrm{sin}(n\,E) + B_n\,\mathrm{cos}(n\,E)) $$

Los coeficientes $A_n$ y $B_n$ son las *amplitudes harmónicas* y están relacionadas a las correcciones que hay que hacer sobre los parámetros de las elipses ajustadas. Nótese que el objetivo del ajuste es encontrar la elipse que minimiza la suma de la serie de Fourier. En un buen ajuste, para $n=1,2,3$ estos coeficientes son muy cercanos a cero, lo cual significa que se convergió a una isofota final.

La aplicación del método en python que utilizaremos es la de [Ellipse](https://photutils.readthedocs.io/en/stable/api/photutils.isophote.Ellipse.html#photutils.isophote.Ellipse.fit_image) de astropy.


### Instalamos e importamos paquetes que usaremos

In [1]:
import astropy
import numpy as np              
import matplotlib.pyplot as plt 
from scipy.optimize import curve_fit
import pandas as pd

# Paquete para abrir/guardar archivos fits y tablas:
from astropy.io import fits,ascii     
from astropy.table import QTable

from astropy.wcs import WCS     # Paquete para trabajar con WCS (World Coordinate System)
import astropy.units as u       # manejo de unidades astronómicas

## herramientas propias de visualización:
from astropy.visualization import ImageNormalize, ZScaleInterval, LinearStretch, simple_norm

from astropy.table import Column  # tarea para manejar tablas de astropy

# paquetes de análisis isofotal:
from photutils.isophote import EllipseGeometry, Ellipse 
from photutils import EllipticalAperture
from photutils.isophote import build_ellipse_model 
plt.style.use('../sisest.mplstyle')
# plt.style.use('ggplot')

### Abrimos los archivos fits

In [2]:
with fits.open('ESO-325-G004_g.fits') as hdul:        # Con "with" podemos leer una archivo y despues borrarlo de la memoria
    hdul.info()
    hdr = hdul[0].header                              # Guardamos el header en la variable hdr
    data = hdul[0].data                               # Guardamos la información de la imagen en un arreglo (matriz de (2202, 2102))
    wcs = WCS(hdr)                                    # Guardamos la información de la transformación de coordenadas

with fits.open('mascara.fits') as hdul:               # lo mismo hacemos con la máscara
    hdul.info()
    data_mask = hdul[0].data                          # la máscara se guarda en data_mask

Filename: ./ESO-325-G004_g.fits
No.    Name      Ver    Type      Cards   Dimensions   Format
  0  PRIMARY       1 PrimaryHDU      71   (2202, 2102)   float32   
Filename: ./mascara.fits
No.    Name      Ver    Type      Cards   Dimensions   Format
  0  PRIMARY       1 PrimaryHDU      35   (2202, 2102)   int32   


the RADECSYS keyword is deprecated, use RADESYSa. [astropy.wcs.wcs]


In [3]:
wcs        # aquí podemos ver la transformación de coordenadas
           # que mapea el espacio de pixeles al espacio de coordenas
           # ascención recta y declinación

WCS Keywords

Number of WCS axes: 2
CTYPE : 'RA---TAN'  'DEC--TAN'  
CRVAL : 205.888333264493  -38.1761110860419  
CRPIX : 1126.0684418684  1053.04437269781  
CD1_1 CD1_2  : -3.17806785208275e-08  4.05739293120765e-05  
CD2_1 CD2_2  : -4.05907257120742e-05  -1.71605584026677e-08  
NAXIS : 2202  2102

In [ ]:
# para ver todo el header de la imagen
hdr

### Estimación Inicial
Para iniciar el método tenemos que dar una primera aproximación a una **isofota**, entonces, con DS9 debemos medir:
- La posición ($x_c,y_c$) del centro de la galaxia, en píxeles.
- El semieje mayor (sma) y semieje menor (b)
- El ángulo de posición (pa)

Con esto vamos a poder dar una medida de la **elipticidad** $\varepsilon$ que es distinta de la excentricidad. La excentricidad es $e= c/a = \sqrt{1-b^2/a^2}$. Mientras que la elipticidad es
$$
\varepsilon = \frac{a-b}{a} = 1 - \frac{b}{a}
$$
es una medida del *achatamiento* de la elipse.


Por último, el ángulo de posición *medido con el DS9* es un ángulo medido desde el eje $x>0$ de la imagen hacia el eje $y>0$, que, si revisamos la documentación, es el *input* que nos pide el código. Sin embargo, debemos pasarlo a radianes.

Es importante notar que el ángulo de posición en el sistema de referencia estándar usado en astronomía se mide desde el Norte hacia el Este. Luego tendremos que corregir el ángulo que mide el DS9 para llevarlo al sistema estándar.

In [5]:
## COMPLETAR
## estimaciones iniciales
## con el software DS9

xc,yc =    ### completar con las coordenadas x,y en pixeles del centro de la galaxia

### estimacion de longitud de a y b:
sma =         # llenar con el semieje mayor a en pixeles
b =           # llenar con el semieje menor b en pixeles

# la elipticidad es 
eps =   #### poner fòrmula de la elipticidad

## el angulo de posicion estimado
pa =   ####### escrbibir el angulo de posicion y PASARLO A RADIANES


In [ ]:
# Chequeamos que este representando bien la forma de la galaxia

aper = EllipticalAperture((xc,yc), sma, b, pa) # define apertura fotométrica elíptica 

fig = plt.figure(figsize=(6,6), dpi=100)
plt.imshow(data, 
           vmin = ,     ####### poner limite mínimo usado en la escala del ds9 para determinar la isofota       
           vmax = ,  ####### poner limite maximo usado en la escala del ds9 para determinar la isofota              
           origin = 'lower', cmap='gray')

aper.plot(color='red') # grafico la elipse

plt.grid(False)
plt.show()

### Visualización con máscara y WCS

Ahora, vamos a desplegar la imagen usando coordenadas ecuatoriales en el plano del cielo ($\alpha,\delta$) utilizando el WCS y además, vamos a visualizar la máscara de fuentes contaminantes. 

In [ ]:
# para obtener un mejor despliegue de la imagen y la máscara

interval = ZScaleInterval() 
vmin, vmax = interval.get_limits(data)                    # Sacamos los límites en cuentas, min  y max.
norm = simple_norm(data, 'sqrt', percent=99.)             # Definimos una función para representar los niveles de brillo
                                                          # cambiando percent entre 0 y 100 cambia el contraste y el brillo

fig = plt.subplots(figsize=(13,6))
ax1 = plt.subplot(121, projection = wcs)                  # Posición del subplot y proyección en coordenadas celestes para los ejes
pos1 = ax1.imshow(data, norm = norm, origin='lower')      # Mostramos la imagen


ax1.set_title('Galaxia Elíptica Gigante ESO 325-G004\n Gemini Sur - GMOS Filtro g\'')

# en este bloque definimos los ejes en coordenadas y especificamos su formato
ra,dec = ax1.coords    

ra.set_axislabel(r'$\alpha$ [h:m:s]', minpad=-2)
dec.set_axislabel(r'$\delta$ [g:m:s]')

ra.set_ticks_position('l')
ra.set_ticklabel_position('l')
ra.set_axislabel_position('l')
dec.set_ticks_position('b')
dec.set_ticklabel_position('b')
dec.set_axislabel_position('b')


ax1.grid(True,color = 'grey', ls = 'solid', alpha = 0.4)       # agregamos grilla

## otra figura al lado
ax2 = plt.subplot(122, projection = wcs)
pos2 = ax2.imshow(data_mask, origin = 'lower')            # Mostramos la máscara
ax2.set_title('Máscara')

plt.show()

In [8]:
# Aplicamos la máscara a la imagen


data_m = np.ma.masked_where(data_mask==1,data,copy=True)  # Función que enmascara en data los pixeles con data_mask==1 y 
                                                          # los guarda en data_m

In [ ]:
# Visualizamos la imagen con la máscara aplcicada
plt.figure(figsize=(6,6))
plt.imshow(  )  # COMPLETAR 

plt.title('Imagen con máscara tapando las fuentes contaminantes')
plt.show()

## Fotometría

Ya tenemos todo para iniciar la fotometría.
Comenzamos  definiendo los objetos *geometry* y *ellipse* con nuestra primera isofota, luego haremos el ajuste completo de la galaxia.

In [10]:
# Definimos isofota inicial como una elipse con los parámetros iniciales
g = EllipseGeometry(xc, yc, sma, eps, pa) 

# Ajustamos el centro de la elipse partiendo de la isofota definida, sobre los datos enmascarados
g.find_center(data_m)

# Definimos el objeto Ellipse como la isofota g aplicada a los datos enmascarados
ellipse = Ellipse(data_m, geometry = g)          

INFO: Found center at x0 = 1124.0, y0 = 1061.0 [photutils.isophote.geometry]



## Ajustamos las isofotas

El proceso se hace de manera automática, dados algunos parámetros y condiciones de contorno (*constrains*).
Vamos a indicarle el semieje mayor mínimo y máximo que pueden tomar las isofotas (<tt>`minsma`</tt> y <tt>`maxsma`</tt>), algunos parámetros de criterios de corte que va a tener el ajuste para poder descartar isofotas con caminos muy ruidosos (<tt>`sclip`</tt> y <tt>`nclip`</tt>) y un parámetro <tt>`maxgerr`</tt> que servirá como un criterio a partir del cual va a dejar la forma de las isofotas *fija* en $\epsilon$ , $(x_c,y_c)$ y <tt>`pa`</tt>, para poder ajustar bien la intensidad en la región donde la galaxia se empieza a confundir con el cielo, y luego llegar al máximo permitido en <tt>`sma`</tt>.

In [12]:
########################################################
###################### ATENCIÓN ########################
#      ¡ Este paso puede demorar varios minutos !      #
#                                                      #
#                                                      #
########################################################
########################################################

isolist = ellipse.fit_image(minsma = 1., maxsma = 1000,
                            sclip = 4., nclip = 4,
                            maxgerr=0.5) 

len(isolist) # que imprima cuántas isofotas logró ajustar.

72

La salida de esto es una **lista de isofotas**, que es en esencia una tabla, que contendrá todos los parámetros de cada isofota producto del ajuste.

In [ ]:
# así podemos ver los nombres de las columnas de isolist
isolist.get_names()

In [ ]:
# vemos la tabla que generó
isolist.to_table()

In [ ]:
# la estructura es similar a un dataframe, podremos acceder a las columnas así:
isolist.pa

Vemos entonces para cada valor del semieje mayor, cúal es el ángulo de posición de las isofotas. Ordenados de menor a mayor sma.

Una lista completa de todos los parámetros que brinda este ajuste se encuentra [aquí](https://photutils.readthedocs.io/en/stable/api/photutils.isophote.IsophoteList.html#photutils.isophote.IsophoteList).

Veamos cómo quedaron las isofotas de la imagen:

In [ ]:
fig = plt.subplots(figsize=(6,6))                             
# para ver pocas:
smas = np.linspace(5, 1000, 15)                               # lista de valores aprox. del semieje mayor (15 valores)
# para ver todas:
# smas = isolist.sma

ax1 = plt.subplot(111)
pos1 = ax1.imshow(data, norm = norm, origin = 'lower')

for sma in smas:
    iso = isolist.get_closest(sma)                            # busca la isofota con el semieje mayor más cercano a sma
    x, y, = iso.sampled_coordinates()                         # genera arreglos con las coord. de los puntos de la isofota
    ax1.plot(x, y, color='white')

plt.show()

Por las características de la visualización en python, ver partes "rectas" en las isofotas es normal, porque está interpolando sobre pedazos de imagen enmascarados.Lo que **no tenemos que ver** son elipses entrecruzadas.

### Modelo de galaxia

Conociendo los valores de intensidad de cada isofota ajustada, se puede construir un modelo del brillo de la galaxia.
Este proceso es una buena manera de verificar que se está haciendo un buen ajuste isofotal, inspeccionando el residuo, verificando que no quede luz que pareciera provenir de la galaxia.

**ATENCIÓN**: Este paso demora mucho (en un servidor lento, puede estar **más de una hora**), por favor mantenerlo comentado si no se lo va a correr, de lo contrario correr toda la notebook va a demorar muchos minutos. 

In [17]:
#########################################################
###################### ATENCIÓN ########################
#########################################################
### descomentar solamente si realmente se quiere ejecutar
#########################################################

#modelo = build_ellipse_model(data_m.shape, isolist, fill=0)     

# Lo construimos con la misma forma de la matriz data2 y utilizando las isofotas ajustadas en Isolist

In [ ]:
## Visualización del modelo y del residuo

# fig, (ax1, ax2, ax3) = plt.subplots(1, 3, figsize=(18, 15))         

# ax1.imshow(data, norm=norm, origin='lower')                         # Visualizamos la imagen original
# ax1.set(title='Imagen original')
# ax2.imshow(modelo, norm=norm, origin='lower')                  # Visualizamos el modelo
# ax2.set(title='Modelo de brillo')
# ax3.imshow(data-modelo, norm=norm, origin='lower')             # Y lo restamos a la imagen obtenida por el telescopio
# ax3.set(title='Residuo')

### Agregamos datos a la tabla

Si bien tenemos una salida de datos muy completa, necesitamos algunos cálculos más.

- El semieje mayor está expresado en píxeles, para poder comparar con otros objetos tomados con otros instrumentos vamos a tener que pasar a una unidad angular.
- Además, no es muy usual usar el semieje mayor de la isofota, sino usar el **radio equivalente**, esto es, el radio que tendría un círculo que tenga la mismo área que la elipse.
  $$r_\mathrm{eq}= a \sqrt{1-\varepsilon}$$
- El ángulo de posición (pa) que introdujimos estaba medido respecto a los ejes de la imagen fits, tenemos que pasarlo al sistema estándar, medido desde el Norte hacia el Este. Analizando la imagen, vemos que esto significa que
    $$ PA_{std} = 180^\circ - PA $$ 
- Por último vamos a calcular el brillo superficial en mag/arcsec$^2$.
    $$ \mu(r)= C_0 - 2.5\,\log_{10}\left(\frac{I(r)}{t\,S^{2}}\right) $$
  donde $I$ es la intensidad de una isofota con un radio equivalente $r$; $S$ la escala del detector; $t$ el tiempo de exposición y 
  $$C_0=k_g * (X - 1)  - A_g + z_g$$ 
  es una constante para pasar al sistema estándar que contempla: el coeficiente de extinción atmosférica $k_g$ en la banda g';  la masa de aire $X$; la absorción interestelar en la banda g' $A_g$;  y el punto cero de la magnitud en la banda g' $z_g$.

Vamos a necesitar algunos datos del header de la imagen:
- La escala del detector, es decir a cuántos arcsec corresponde un pixel.
- La masa de aire al momento de tomar la imagen.
- El tiempo de exposición de la observación.

In [ ]:
# para acceder a esos valores sólo tenemos que buscar el "keyword" del header
# y accederlo como si fuera un dataframe:

hdr['PIXSCALE']

In [ ]:
# guardamos los datos que vamos a necesitar


scale = hdr['PIXSCALE']
exptime = hdr[   ]     ### Completar con el keyword del header que corresponde                                          
airmass = hdr[   ]     ### Completar con el keyword del header que corresponde     

scale,exptime,airmass

In [ ]:
# Sumamos los datos dados en el enunciado:
# Completar:
kg =
zg = 
Ag =

In [ ]:
# agregamos columnas en el objeto isolist

isolist.smarcsec =   # completar la expresión para obtener el semieje mayor en arcosegudos 

isolist.req =        # completar la expresión para obtener el radio equivalente en arcosegundos
 
isolist.pa_std =     # completar la expresión para obtener el ángulo de posicion en el sistema estandar, en grados
isolist.pa_std_err = # completar la expresión para obtener el error del ángulo de posición en grados

isolist.mu =         # completar la expresión para obtener el brillo sup. en el sistema estandar


Podemos agregar el error en el brillo superficial $\mu$ por propagación de errores.

Dada una variable $z$ resultado de aplicar una función $f$ sobre $n$ variables con errores, o sea $z=f(x_1,x_2,\dots,x_n)$, el error $|\Delta z|$ se puede estimar como:
$$ |\Delta z | \ \lessapprox \sum_{i=1}^n \left|\frac{\partial f}{\partial x_i}\right|_{\tilde{x_1},\dots} \cdot |\Delta x_i | $$

Donde los $|\Delta x_i |$ son los errores de cada variable y $\tilde{x_i}$ las estimaciones de dichas variables.

Para el caso del brillo superficial:
$$ |\Delta \mu | \lessapprox \frac{2.5}{I \ln(10)}  |\Delta I| $$

In [ ]:
## puedo agregar el error en brillo superficial por propagación de errores 

isolist.mu_err =   ### completar la expresión


## Guardamos los resultados obtenidos

Hasta acá, tenemos todos los datos para poder hacer lo que queda de la fotometría y análisis. Como demora mucho el proceso de ajuste de isofotas, si están conformes con el ajuste obtenido, propongo que **guardemos esa tabla en un archivo**, de esa manera, al volver a abrir la notebook no necesitamos volver a correr esa parte del código, sólo tendremos que abrir y leer una tabla, que ya sabemos hacer y tarda menos de un segundo. 

In [ ]:
# guardamos en una tabla de astropy TODAS las columnas de nuestra tabla

tabla=isolist.to_table(isolist.get_names()) ## las de isolist

# agregamos las que sumamos nosotros

add={'req' :        isolist.req,
     'smarcsec' :   isolist.smarcsec,
     'mu' :         isolist.mu,
     'mu_err' :     isolist.mu_err,
     'pa_std' :     isolist.pa_std,
     'pa_std_err' : isolist.pa_std_err
    }

for k in add.keys():
    tabla[k]=add[k]

# Esa tabla la grabamos en un archivo

fname = 'isolist.dat'
ascii.write(tabla,fname,overwrite=True)
#########################################################
###################### ATENCIÓN #########################
#########################################################
# Está el overwrite verdadero, esto significa que va a  #
# sobreescribir el archivo cuando se corra. Ojo de no   #
#      perder información que se quiera guardar !       #
#########################################################


## Leemos la tabla con la fotometría
Ahora que tenemos nuestro archivo con los resultados de la fotometría, recuerden comentar esta última celda y las celdas que hacen el ajuste (todas las que están dentro de la sección fotometría), así no lo vuelven a hacer cuando reinicien el *kernel*, y no sobreescriben ni pierden tiempo. 

In [ ]:
# para leer la tabla hacemos
isolist = QTable.read(fname,format='ascii')  ## pasamos a un objeto Qtable
isolist=pd.DataFrame(np.array(isolist))  ## pasamos a un DataFrame con el que ya hemos trabajado


In [ ]:

isolist.keys() # chequeamos que copió todo

## Análisis
### Graficamos la variación de los parámetros isofotales

In [ ]:
# Graficamos la elipticidad en función del radio equivalente


In [ ]:
# Graficamos el ángulo de posición en función del radio equivalente


In [ ]:
# Graficamos la amplitud B4 en función del radio equivalente


In [ ]:
# Graficamos la variación de las coordenadas del centro (x,y) en función del radio equivalente


### Vemos los perfiles de flujo y del brillo superficial


In [ ]:
# Graficamos la curva de crecimiento del flujo


Vamos a estimar el radio efectivo $r_{ef}$ de nuestra fotometría, recordamos que está definido como el radio equivalente correspondiente a la mitad del flujo integrado.

In [ ]:
flux_max =        # calculamos flujo máximo
flux_ef =         # y el correspondiente al r_ef

# buscamos la línea de la tabla que contiene un flujo lo más parecido posible a flux_ef
ind_ref = (  np.abs(flux_ef-isolist.tflux_e)  ).argmin()
# esto es, de la diferencia absoluta entre el flux_ef y la de cada elemento de la tabla, toma la línea donde está el mínimo, y guarda *el índice*
# consideramos el radio equivalente en esa línea como el radio efectivo
r_ef = isolist.req[ind_ref]  


print('Flujo máximo = ', flux_max)
print('r_ef = ', round(r_ef,1), 'arcsec' )

Ahora lo marcamos en la curva de crecimiento del flujo.

In [ ]:
fig = plt.figure( )

plt.scatter() ### grafico de la curva de crecimiento del flujo

plt.hlines( flux_ef,                     # línea horizontal que marca el flujo efectivo
           0.,
           150.,  # variar de ser necesario este valor
           linestyles = 'dashed',
           color='C7',
           label = '$F_{max}$/2')

plt.vlines( r_ef,                        # línea vertical que marca el radio efectivo
           0., flux_ef,
           color='C7',
           linestyles = 'dotted')

plt.text( r_ef,flux_ef/2,
         r'$r_{ef}$',c='C7',ha='left')   # etiqueta para el radio efectivo


plt.title(  )  # completar 
plt.xlabel(  ) # completar 
plt.ylabel(   )  # completar 

plt.legend()
plt.show()


Ahora, graficamos el perfil de brillo superficial.

In [ ]:
# Figura con el perfil de brillo superficial


In [ ]:
# vamos a tomar el mu_ef como el mu equivalente al radio efectivo, este será:

mu_ef = isolist.mu[ind_ref]  

print('mu_ef = ', round(mu_ef,1), 'mag/arcsec^2' )

In [ ]:
# podemos marcar el r_ef y mu_ef en el perfil de brillo superficial como hicimos con la curva de crecimiento


Estimamos la magnitud total de la galaxia en la banda g' usando el flujo total y la ley de Pogson. 

Esto es,
$$ m = -2.5 \log\left( \frac{F}{t} \right) - C_0 $$

In [ ]:
# cálculo de la magnitud total

m_tot =  ### completar la expresión 

print('m_tot =', round(m_tot, 1) )


### Ajuste de Sèrsic

Para complementar estas estimaciones, vamos a modelar el perfil de brillo superficial de la galaxia con una Ley de Sèrsic, de la forma:
$$ \mu(r)= \mu_\mathrm{ef} + \left({1.086\,b_n}\right)\left[\left(\frac{r}{R_\mathrm{ef}}\right)^{(1/n)}-1\right] $$

Donde $R_\mathrm{ef}$ es el radio efectivo de la galaxia, $\mu_\mathrm{ef}$ el brillo superficial al radio $R_\mathrm{ef}$, $n$ el índice de Sérsic, y $b_n$ es un parámetro asociado a $n$ que sigue la expresión aproximada $b_n=1.9992\,n-0.3271$ para $0.5<n<10$ [(Graham, A. W. et al, 2008)](https://ui.adsabs.harvard.edu/abs/2008MNRAS.388.1708G}) a fin de asegurar que la mitad del flujo total esté dentro del $R_\mathrm{ef}$. 

Notemos que como usamos brillo superficial, la expresión de la ley es diferente a la vista en la teoría, que está expresada en función de la intensidad.


In [ ]:
# Definimos la función de Sérsic
def sersic(r,muef,n,Ref):
    bn = 1.9992 * n - 0.3271
    mu = muef + (1.086 * bn) * (  np.power((r/Ref),1./n) - 1. )
    return mu


Ajustamos el perfil de Sérsic.


In [ ]:
[mu_eff,n,Ref],cov=curve_fit(  ) ## completar con: modelo funcional, variable independiente, variable dependiente 

print('mu_ef =', round(mu_eff,1), 'mag/arcsec^2  ', 'n =', round(n,1) , '  R_ef =', round(Ref,1) , 'arcsec')

Observamos que parece cambiar bastante la estimación de $r_{ef}$, pero no tanto la de $\mu_{ef}$.

Verificamos el ajuste graficando.

In [ ]:
# perfil de brillo superficial

fig = plt.figure(figsize = (8,6))

r_=np.linspace(0,120,200)

plt.plot( isolist.req,
             isolist.mu,
             '.',label='Datos')

plt.plot(r_,sersic(r_,mu_eff,n,Ref),c='C1',label='Perfil de Sersic')
plt.gca().invert_yaxis()
plt.title('Perfil de brillo superficial')
plt.xlabel('$r$ [arcsec]')
plt.ylabel('$\mu_g$ [mag/arcsec$^2$]')
plt.legend()
plt.show()


También se puede estimar la magnitud intrínseca de la banda g' con esta fórmula (está por alguna parte del apunte de extragaláctica)
$$  {m}_0 = \mu_\mathrm{eff}-1.995450-5~\log(R_\mathrm{eff})-1.0857~b_n-2.5~\log\left[b_n^{-2n}~n\Gamma(2n)\right] $$
 con $\Gamma(2n)$  la función gamma, que la llamamos con scipy

In [ ]:
from scipy.special import gamma 

m = mu_eff - 1.995450 - 5. * np.log10(Ref) - 1.0857 * (1.9992 * n - 0.3271) - 2.5 * np.log10( np.power(1.9992 * n - 0.3271,-2.*n) * n * gamma(2*n) )

print('nueva estimación de la mag. total m =', round(m,2) , '   estimación anterior m_tot=', round(m_tot,2))


FIN